# [WatchPAT ONE](https://www.itamar-medical.com/professionals/disposable-hsawatchpat-one/) nRF52832 Fault Injection

Joe Grand ([@joegrand](https://twitter.com/joegrand), [Grand Idea Studio](http://www.grandideastudio.com))

Based on prior work by [LimitedResults](https://twitter.com/LimitedResults), [Colin O'Flynn](https://twitter.com/colinoflynn), [Thomas Roth (stacksmashing)](https://twitter.com/ghidraninja), and [Lennert Wouters](https://twitter.com/lennertwo)

Requires the [ChipWhisperer](https://www.newae.com/chipwhisperer) and [Segger J-Link](https://www.segger.com/products/debug-probes/j-link/)

## References

* [nRF52 Debug Resurrection (APPROTECT Bypass) Part 1](https://limitedresults.com/2020/06/nrf52-debug-resurrection-approtect-bypass/)
* [nRF52 Debug Resurrection (APPROTECT Bypass) Part 2](https://limitedresults.com/2020/06/nrf52-debug-resurrection-approtect-bypass-part-2/)
* [airtag-re GitHub repo](https://github.com/colinoflynn/airtag-re)
* [How the Apple AirTags were hacked](https://www.youtube.com/watch?v=_E0PWQvW-14)


## Connections

| ChipWhisperer              | Target            | Notes                                                  |
|:---------------------------|:------------------|:-------------------------------------------------------|
| +3.3V (pin 3)              | TP2               | VBAT, Battery input, 1.5V to 3.3V max. (top red wire)  |
| TIO4 (pin 16)              | TP49              | VDD_nRF, Output of boost converter (middle red wire)   |
| GND (pin 2)                | Battery (-)       | Through hole pad near C72/C73 (black wire)             |
| SMA Measure & Glitch       | DEC1 (nRF pin 1)  | 0.9V internal LDO decoupling, remove C62 capacitor     |
|                            |                   | Used for side channel analysis (SCA) and glitching     |

| Segger J-Link              | Target            | Notes                                                  |
|:---------------------------|:------------------|:-------------------------------------------------------|
| VTref (pin 1)              | TP49              | VDD_nRF, Output of boost converter (middle red wire)   |
| SWDIO (pin 7)              | TP282             | ARM Serial Wire Debug (SWD) Bidirectional I/O          |
| SWCLK (pin 9)              | TP283             | ARM Serial Wire Debug (SWD) Clock (from host)          |
| GND (pin 4, 6, 8, 10, 12)  | Battery (-)       | Through hole pad near C72/C73 (black wire)             |


## Photos

<table><tr>
    <td><img src="watchpat-front.jpg" style="height: 600px;" title="WatchPAT One Wiring Front Side"/></td>
    <td><img src="watchpat-back.jpg" style="height: 600px;" title="WatchPAT One Wiring Back Side"/></td>
</tr></table>

<img src="watchpat-complete.jpg" style="width: 934px;" title="WatchPAT One Complete Setup"/></td>

## Initial setup

In [1]:
import sys
import subprocess

import itertools  
from bokeh.plotting import figure, show
from bokeh.io import output_notebook, push_notebook
from bokeh.palettes import Dark2_5 as palette

import time
import os
import numpy as np
from tqdm.notebook import tqdm

import chipwhisperer as cw

In [2]:
scope = cw.scope()                    # Automatically detect and connect to ChipWhisperer
scope.default_setup()                 # Set default configuration values

print("ChipWhisperer SN:", scope.sn)

See https://chipwhisperer.readthedocs.io/en/latest/api.html#firmware-update


ChipWhisperer SN: 50203120355448513330343238313034


In [3]:
# ChipWhisperer configuration
scope.adc.samples = 24000                 # Number of ADC samples to record in a single capture
scope.adc.offset = 0                      # Number of samples to skip before recording data after trigger event
scope.adc.basic_mode = "rising_edge"      # ADC capture trigger
scope.clock.adc_src = "clkgen_x1"         # CLKGEN output via Digital Clock Manager (DCM) block (no multiplier)

scope.trigger.triggers = "tio4"           # Trigger on TIO4
scope.io.glitch_lp = False                # Disable low power glitch
scope.io.glitch_hp = False                # Disable high power glitch
scope.io.hs2 = None                       # Do not route clock signal to HS2 pin

scope.clock.clkgen_freq = 100000000       # Set CLKGEN to 100MHz
scope.glitch.clk_src = "clkgen"           # Glitch input clock
scope.glitch.trigger_src = "ext_single"   # Glitch only after scope.arm() called
scope.glitch.output = "enable_only"       # Insert glitch for entire clock cycle (beneficial when asynchronous to the target)

scope.gain.db = 10                        # Set gain of the low-noise amplifier
scope.adc.decimate = 20                   # ADC downsampling (record sample every 20 clocks)
scope.adc.presamples = 0                  # Number of samples to record from before the trigger event

scope.io.target_pwr = True                # Enable power to target

## Determining glitch offset

As discovered by [LimitedResults](https://limitedresults.com/2020/06/nrf52-debug-resurrection-approtect-bypass/), the desired glitch range is the section of activity ~2uS before the dip in CPU power (measured from DEC1).

<img src="watchpat-reference.png" style="width: 934px;" title="WatchPAT One Power Analysis Reference"/></td>
<br>

In [4]:
# Side channel power analysis
traces = np.zeros((10, scope.adc.samples), dtype='float64')

for i in tqdm(range(10)):
    scope.io.target_pwr = False           # Power cycle the target
    time.sleep(0.75)                      # Delay to ensure proper capacitor discharge/system reset
    scope.arm()                           # Arm the ADC, wait for trigger
    scope.io.target_pwr = True
    
    scope.capture()                       # Capture trace
    traces[i] = scope.get_last_trace()    # Add to our capture buffer
    
    time.sleep(0.05)
    
scope.io.target_pwr = False               # Disable power to target

  0%|          | 0/10 [00:00<?, ?it/s]

In [5]:
# Look for the dip in measured trace to identify the glitch offset range
output_notebook()

# Setup plot
p = figure(sizing_mode = 'scale_width', plot_height = 300, plot_width = 900)
x_range = range(0, traces.shape[1])
colors = itertools.cycle(palette) 

# Plot capture results
for i, color in zip(range(10), colors):
    p.line(x_range, traces[i], color = color, legend = str(i))

p.line(x_range, np.mean(traces, axis = 0), color = 'blue', legend = 'mean')
    
p.legend.click_policy = "hide"
show(p)

Loading BokehJS ...

## Performing the glitch

In [6]:
# Set range of glitch offset (in cycles)
# Multiplied by 20 to account for decimation (ADC downsampling) in previous phase
offset_start = 6500 * 20
offset_end = 6600 * 20

# Set width of glitch pulse (in cycles)
scope.glitch.repeat = 15

In [7]:
# Additional ChipWhisperer configuration
scope.io.hs2 = "glitch"                     # Route output of the glitch module to HS2 pin
scope.glitch.arm_timing = "before_scope"    # Arm glitch module before scope is armed
scope.adc.decimate = 1                      # Disable ADC downsampling

scope.io.target_pwr = True                  # Enable power to target

In [8]:
# Command line string to invoke J-Link
cmd = '/Applications/SEGGER/JLink/JLinkExe -autoconnect 1 -Device NRF52832_XXAA -If SWD -NoGui 1 -Speed 1000 -ExitOnError 1'

In [9]:
# Connect to J-Link and capture baseline response when no device is detected
process = subprocess.Popen(cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.stdout.read()
print(output)

ref = output

b'SEGGER J-Link Commander V7.60a (Compiled Dec 16 2021 10:34:46)\nDLL version V7.60a, compiled Dec 16 2021 10:34:39\n\nJ-Link Commander will now exit on Error\nConnecting to J-Link via USB...O.K.\nFirmware: J-Link V9 compiled May  7 2021 16:26:12\nHardware version: V9.30\nS/N: 609303587\nLicense(s): RDI, FlashBP, FlashDL, JFlash, GDB\nVTref=3.309V\nDevice "NRF52832_XXAA" selected.\n\n\nConnecting to target via SWD\nInitTarget() start\nCTRL-AP indicates that the device is secured.\nFor debugger connection the device needs to be unsecured.\nNote: Unsecuring will trigger a mass erase of the internal flash.\n\nExecuting default behavior previously saved in the registry.\nSkipping unsecure.\nInitTarget() end\nInitTarget() start\nCTRL-AP indicates that the device is secured.\nFor debugger connection the device needs to be unsecured.\nNote: Unsecuring will trigger a mass erase of the internal flash.\n\nExecuting default behavior previously saved in the registry.\nSkipping unsecure.\nInitTarge

In [10]:
print("Glitch width: %d"%scope.glitch.repeat)
print("Glitch offset range: %4d, %4d"%(offset_start, offset_end))

scope.io.glitch_lp = True    # Enable low power glitch

for offset in tqdm(range(offset_start, offset_end)):
    scope.glitch.ext_offset = offset    # Offset (in cycles) after trigger event before inserting glitch
    
    try:
        scope.io.target_pwr = False     # Power cycle the target
        time.sleep(0.75)                # Delay to ensure proper capacitor discharge/system reset
        scope.arm()                     # Arm the ADC, wait for trigger
        scope.io.target_pwr = True
        time.sleep(0.05)
            
        process = subprocess.Popen(cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        output = process.stdout.read()
            
        # If J-Link response is different than our baseline, we've successfully enabled debug!
        # Ignore the initial start-up text (381 characters), since VTref can vary slightly
        if output[381:] != ref[381:]:
            print(output)
            break

    except KeyboardInterrupt:
        break

Glitch width: 15
Glitch offset range: 130000, 132000


  0%|          | 0/2000 [00:00<?, ?it/s]

b'SEGGER J-Link Commander V7.60a (Compiled Dec 16 2021 10:34:46)\nDLL version V7.60a, compiled Dec 16 2021 10:34:39\n\nJ-Link Commander will now exit on Error\nConnecting to J-Link via USB...O.K.\nFirmware: J-Link V9 compiled May  7 2021 16:26:12\nHardware version: V9.30\nS/N: 609303587\nLicense(s): RDI, FlashBP, FlashDL, JFlash, GDB\nVTref=3.314V\nDevice "NRF52832_XXAA" selected.\n\n\nConnecting to target via SWD\nInitTarget() start\nInitTarget() end\nFound SW-DP with ID 0x2BA01477\nDPIDR: 0x2BA01477\nCoreSight SoC-400 or earlier\nScanning AP map to find all available APs\nAP[2]: Stopped AP scan as end of AP map has been reached\nAP[0]: AHB-AP (IDR: 0x24770011)\nAP[1]: JTAG-AP (IDR: 0x02880000)\nIterating through AP map to find AHB-AP to use\nAP[0]: Core found\nAP[0]: AHB-AP ROM base: 0xE00FF000\nCPUID register: 0x410FC241. Implementer code: 0x41 (ARM)\nFound Cortex-M4 r0p1, Little endian.\nFPUnit: 6 code (BP) slots and 2 literal slots\nCoreSight components:\nROMTbl[0] @ E00FF000\n[0]

## Firmware extraction

In [12]:
import shlex

# Command line string to dump memory/extract firmware
cmd = 'openocd -f interface/jlink.cfg -c "transport select swd" -f target/nrf52.cfg -c "init" -c "dump_image dump.bin 0x0 524288" -c "exit"'
#cmd = 'nrfjprog --readcode dump.hex'

result = subprocess.run(shlex.split(cmd), capture_output=True, text=True)
print(result.stderr)

Open On-Chip Debugger 0.11.0+dev-00380-gf24a283ac (2021-09-06-19:19)
Licensed under GNU GPL v2
For bug reports, read
	http://openocd.org/doc/doxygen/bugs.html
swd
Info : J-Link V9 compiled May  7 2021 16:26:12
Info : Hardware version: 9.30
Info : VTarget = 3.311 V
Info : clock speed 1000 kHz
Info : SWD DPIDR 0x2ba01477
Info : nrf52.cpu: hardware has 6 breakpoints, 4 watchpoints
Info : starting gdb server for nrf52.cpu on 3333
Info : Listening on port 3333 for gdb connections
dumped 524288 bytes in 9.751814s (52.503 KiB/s)




In [13]:
# Clean up
scope.io.glitch_lp = False
scope.io.glitch_hp = False
scope.io.target_pwr = False
scope.dis()
print("Done!")

Done!
